# Quickstart

[**User Guide**](https://millerbrainobservatory.github.io/LBM-Suite2p-Python/user_guide.html) | 
[**Supported Filetypes**](https://millerbrainobservatory.github.io/mbo_utilities/array_types.html#quick-reference) | 
[**API Reference**](https://millerbrainobservatory.github.io/LBM-Suite2p-Python/api.html) | 
[**MBO Hub**](https://millerbrainobservatory.github.io/)

Suite2p-based calcium imaging pipeline for Light Beads Microscopy data.

The only required parameter is the input data.

`input_data` can be any filepath or Lazy Array supported by [imread](https://millerbrainobservatory.github.io/mbo_utilities/user_guide.html#reading-and-writing-data).

In [ ]:
import lbm_suite2p_python as lsp

ops = {
    "diameter": 4,
    "anatomical_only": 4,
    "accept_all_cells": True,
    "spatial_hp_cp": 3,
    "denoise": 1,
    "two_step_registration": 1,
}

input_data = r"D:\demo\raw"
save_path = r"D:\demo\results"

results = lsp.pipeline(
    input_data=input_data,      # path to .zarr, .tiff, or .bin file
    save_path=save_path,        # default: save next to input file
    ops=ops,                    # default: use MBO-optimized parameters
    planes=1,                   # process single plane (1-indexed)
    roi=None,                   # default: stitch multi-ROI data
    keep_reg=True,              # default: keep data.bin (registered binary)
    keep_raw=False,             # default: delete data_raw.bin after processing
    force_reg=False,            # default: skip if already registered
    force_detect=False,         # default: skip if stat.npy exists
    num_frames=None,            # default: use all frames
    dff_window_size=None,       # default: auto-calculate from tau and framerate
    dff_percentile=20,          # default: 20th percentile for baseline
    dff_smooth_window=None,     # default: auto-calculate from tau and framerate
    reader_kwargs={
        "fix_phase": True,      # default: MboRawArrays correct phase by default
        "use_fft": True,        # default: MboRawArrays use FFT default
    },
)

## Load Results

In [ ]:
results = lsp.load_planar_results(ops_files[0])

F = results["F"]           # (n_rois, n_frames)
Fneu = results["Fneu"]     # (n_rois, n_frames)
stat = results["stat"]     # ROI stats
iscell = results["iscell"] # (n_rois, 2)

print(f"ROIs: {len(stat)}, Accepted: {iscell[:, 0].sum():.0f}")

## Compute ΔF/F

In [ ]:
iscell_mask = iscell[:, 0].astype(bool)
F_cells = F[iscell_mask]

dff = lsp.dff_rolling_percentile(
    F_cells,
    window_size=300,  # 10 × tau × framerate
    percentile=20,
)

## Suite2p GUI

In [ ]:
from suite2p import gui
gui.run(statfile=str(ops_files[0].parent / "stat.npy"))

In [2]:
import lbm_suite2p_python as lsp
import matplotlib.pyplot as plt

# basic usage
fig = lsp.plot_3d_rastermap_clusters("D:/demo/results/suite2p")
plt.show()

# with custom clusters
# fig = lsp.plot_3d_rastermap_clusters("D:/demo/results/suite2p", n_clusters=50)

# save to file
# fig = lsp.plot_3d_rastermap_clusters("D:/demo/results/suite2p", save_path="rastermap_clusters.png")


<Figure size 1400x1000 with 0 Axes>

---

## What's Next

- [User Guide](https://millerbrainobservatory.github.io/LBM-Suite2p-Python/user_guide.html) - Parameters, outputs, troubleshooting
- [Grid Search](https://github.com/MillerBrainObservatory/LBM-Suite2p-Python/blob/master/dev/grid_search.ipynb) - Optimize parameters
- [Postprocessing](https://millerbrainobservatory.github.io/LBM-Suite2p-Python/postprocessing.html) - Filters and quality metrics